Master Notebook for Hugging Face repos Upload and Download V3

Latest version on : https://www.patreon.com/posts/104672510

In [ ]:
!pip install huggingface_hub --upgrade

!pip install ipywidgets --upgrade

Use below cell to paste your Hugging Face token key. 

Access Tokens are here : https://huggingface.co/settings/tokens

In [ ]:
# Use this cell to enter your Hugging Face token and authenticate 

hugging_face_token = 'your_HF_Token'

!export HUGGING_FACE_HUB_TOKEN=hugging_face_token

import subprocess

# Command to log in using the token
command = ['huggingface-cli', 'login', '--token', hugging_face_token]

# Execute the command
subprocess.run(command, check=True)

In [ ]:
# This cell is used to upload single file into a repo with certain name

from huggingface_hub import HfApi
api = HfApi()
api.upload_file(
    path_or_fileobj=r"/home/Ubuntu/apps/stable-diffusion-webui/models/Stable-diffusion/model_name.safetensors",
    path_in_repo="model_name.safetensors",
    repo_id="YourUserName/reponame",
    repo_type="model",
)

In [ ]:
# This cell is used to upload a folder into a repo with single commit

from huggingface_hub import HfApi
api = HfApi()
api.upload_folder(
    folder_path=r"/home/Ubuntu/apps/stable-diffusion-webui/models/Stable-diffusion",
    repo_id="YourUserName/reponame",
    repo_type="model",
)

To upload all files in given folder to the target Hugging Face repository use below

In [ ]:
# This cell uploads a folder into remote repo with multi commit
# Supports continue feature so if gets interrupted you can run again to continue / resume

from huggingface_hub import HfApi
from huggingface_hub import get_collection, delete_collection_item
from huggingface_hub import upload_file
from huggingface_hub import (
    HfFolder,
    ModelCard,
    ModelCardData,
    create_repo,
    hf_hub_download,
    upload_folder,
    whoami,
)
api = HfApi()
upload_folder(
    folder_path=r"/home/Ubuntu/apps/stable-diffusion-webui/models/Stable-diffusion",
    repo_id="YourUserName/reponame",
    repo_type="model",
    multi_commits=True,
    multi_commits_verbose=True,
)


To download all files in given Hugging Face repository use below

In [ ]:
import os
import requests
import hashlib
from huggingface_hub import list_repo_files, hf_hub_url, hf_hub_download
from huggingface_hub.utils import HfFolder
from tqdm import tqdm

def calculate_file_hash(file_path):
    sha256_hash = hashlib.sha256()
    with open(file_path, "rb") as f:
        for byte_block in iter(lambda: f.read(4096), b""):
            sha256_hash.update(byte_block)
    return sha256_hash.hexdigest()

def download_file(url, target_path, headers, expected_size=None):
    response = requests.get(url, headers=headers, stream=True)
    response.raise_for_status()

    total_size = int(response.headers.get('content-length', 0))
    mode = 'ab' if os.path.exists(target_path) else 'wb'
    
    with tqdm(total=total_size, unit='B', unit_scale=True, desc=os.path.basename(target_path), initial=0, ascii=True) as pbar:
        with open(target_path, mode) as f:
            for chunk in response.iter_content(chunk_size=8192):
                if chunk:
                    f.write(chunk)
                    pbar.update(len(chunk))

    if expected_size and os.path.getsize(target_path) != expected_size:
        raise ValueError(f"Size mismatch for {target_path}. Expected: {expected_size}, Got: {os.path.getsize(target_path)}")

# Define the repository and target folder
repo_id = "YourUserName/reponame"
target_folder = "/home/Ubuntu/apps/stable-diffusion-webui/models/Stable-diffusion"

# Retrieve the token from the .huggingface folder or set it manually
token = HfFolder.get_token()
if not token:
    raise ValueError("Hugging Face token not found. Please log in using `huggingface-cli login` or set the token manually.")

headers = {"Authorization": f"Bearer {token}"}

# List all files in the repository
files = list_repo_files(repo_id)

# Ensure the target folder exists
os.makedirs(target_folder, exist_ok=True)

# Download each file directly to the target folder
for file in files:
    try:
        target_path = os.path.join(target_folder, file)
        
        # Get file metadata
        file_info = hf_hub_download(repo_id, filename=file, repo_type='model', token=token, local_dir=target_folder, local_dir_use_symlinks=False)
        expected_size = os.path.getsize(file_info)

        # Check if the file already exists and has the correct size
        if os.path.exists(target_path):
            if os.path.getsize(target_path) == expected_size:
                print(f"File {file} already exists and is complete. Skipping download.")
                continue
            else:
                print(f"File {file} exists but is incomplete. Resuming download.")

        # Get the URL for the file
        file_url = hf_hub_url(repo_id, filename=file, repo_type='model')
        
        # Ensure subdirectories exist
        os.makedirs(os.path.dirname(target_path), exist_ok=True)
        
        # Download the file with authentication and size verification
        download_file(file_url, target_path, headers, expected_size)
        
        # Set the correct permissions for the downloaded file
        os.chmod(target_path, 0o644)  # Read and write for owner, read for group and others
    
    except Exception as e:
        print(f"An error occurred while processing file {file}: {e}")

print(f"All files have been downloaded and verified in {target_folder}")

In [ ]:
# This cell downloads a specific subdirectory from a given repo

!pip install tqdm --upgrade

import os
import requests
from huggingface_hub import list_repo_files, hf_hub_url
from huggingface_hub.utils import HfFolder
from tqdm import tqdm

# Define the repository, subdirectory, and target folder
repo_id = "YourUserName/reponame" # example: MonsterMMORPG/kohya_new_test
subdirectory = "path/to/subdirectory" # example: 6e_6
target_folder = "/home/Ubuntu/apps/stable-diffusion-webui/models/Stable-diffusion"

# Retrieve the token from the .huggingface folder or set it manually
token = HfFolder.get_token()
# or set your token directly
# token = "your_huggingface_token"

if not token:
    raise ValueError("Hugging Face token not found. Please log in using `huggingface-cli login` or set the token manually.")

headers = {
    "Authorization": f"Bearer {token}"
}

# List all files in the repository
files = list_repo_files(repo_id)

# Ensure the target folder exists
os.makedirs(target_folder, exist_ok=True)

# Filter files to only include those in the specified subdirectory
subdirectory_files = [file for file in files if file.startswith(subdirectory + '/')]

# Download each file directly to the target folder
for file in subdirectory_files:
    try:
        # Define the target path for the file
        target_path = os.path.join(target_folder, os.path.relpath(file, subdirectory))
        
        # Check if the file already exists
        if os.path.exists(target_path):
            print(f"File {file} already exists. Skipping download.")
            continue
        
        # Get the URL for the file
        file_url = hf_hub_url(repo_id, filename=file, repo_type='model')
        
        # Ensure subdirectories exist
        os.makedirs(os.path.dirname(target_path), exist_ok=True)
        
        # Download the file with authentication
        response = requests.get(file_url, headers=headers, stream=True)
        response.raise_for_status()  # Raise an error for bad status codes
        
        # Get the total file size from the response headers
        total_size = int(response.headers.get('content-length', 0))
        
        # Progress bar setup
        with tqdm(total=total_size, unit='B', unit_scale=True, desc=file, initial=0, ascii=True) as pbar:
            # Write the file to the target path
            with open(target_path, 'wb') as f:
                for chunk in response.iter_content(chunk_size=8192):
                    if chunk:
                        f.write(chunk)
                        pbar.update(len(chunk))
        
        # Set the correct permissions for the downloaded file
        os.chmod(target_path, 0o644)  # Read and write for owner, read for group and others
    
    except Exception as e:
        print(f"An error occurred while processing file {file}: {e}")

print(f"All files from the subdirectory '{subdirectory}' have been downloaded to {target_folder}")

In [ ]:
# This cell downloads a specific file from a given repo

!pip install tqdm --upgrade

import os
import requests
from huggingface_hub import hf_hub_url
from huggingface_hub.utils import HfFolder
from tqdm import tqdm

# Define the repository, file path, and target folder
repo_id = "YourUserName/reponame" # example: MonsterMMORPG/kohya_new_test
file_path = "path/to/your/file.ext" # example: 6e_6/9e_6_TE_1e_6.safetensors download model file inside 6e_6 folder
target_folder = "/home/Ubuntu/apps/stable-diffusion-webui/models/Stable-diffusion"

# Retrieve the token from the .huggingface folder or set it manually
token = HfFolder.get_token()
# or set your token directly
# token = "your_huggingface_token"

if not token:
    raise ValueError("Hugging Face token not found. Please log in using `huggingface-cli login` or set the token manually.")

headers = {
    "Authorization": f"Bearer {token}"
}

# Ensure the target folder exists
os.makedirs(target_folder, exist_ok=True)

# Define the target path for the file
target_path = os.path.join(target_folder, os.path.basename(file_path))

# Check if the file already exists
if os.path.exists(target_path):
    print(f"File {file_path} already exists. Skipping download.")
else:
    try:
        # Get the URL for the file
        file_url = hf_hub_url(repo_id, filename=file_path, repo_type='model')
        
        # Download the file with authentication
        response = requests.get(file_url, headers=headers, stream=True)
        response.raise_for_status()  # Raise an error for bad status codes
        
        # Get the total file size from the response headers
        total_size = int(response.headers.get('content-length', 0))
        
        # Progress bar setup
        with tqdm(total=total_size, unit='B', unit_scale=True, desc=os.path.basename(file_path), initial=0, ascii=True) as pbar:
            # Write the file to the target path
            with open(target_path, 'wb') as f:
                for chunk in response.iter_content(chunk_size=8192):
                    if chunk:
                        f.write(chunk)
                        pbar.update(len(chunk))
        
        # Set the correct permissions for the downloaded file
        os.chmod(target_path, 0o644)  # Read and write for owner, read for group and others
    
    except Exception as e:
        print(f"An error occurred while processing file {file_path}: {e}")

print(f"The file '{file_path}' has been downloaded to {target_folder}")